In [2]:
import os
import numpy as np
import tensorflow as tf
from tensorflow.image import resize
import librosa
from IPython.display import Audio,display

In [3]:
model = tf.keras.models.load_model("model.keras")

C:\Users\rizzh\anaconda3\Lib\site-packages\keras\src\saving\saving_lib.py:802: UserWarning: Skipping variable loading for optimizer 'rmsprop', because it has 26 variables whereas the saved optimizer has 50 variables. 
  saveable.load_own_variables(weights_store.get(inner_path))


In [4]:
classes = ['blues', 'classical', 'country', 'disco', 'hiphop', 'jazz', 'metal', 'pop', 'reggae', 'rock']

In [5]:
def preprocessdata(file_path,target_shape=(148,148)):
    data = []
    audio_data,sample_rate = librosa.load(file_path,sr = None)
    chunk_duration = 4 
    overlap_duration = 2 
    chunk_samples = chunk_duration*sample_rate
    overlap_samples = overlap_duration*sample_rate
    num_chunks = int(np.ceil((len(audio_data)-chunk_samples)/(chunk_samples-overlap_samples))) + 1
    for i in range(num_chunks):
        start = i*(chunk_samples-overlap_samples)
        end = start + chunk_samples
        chunk = audio_data[start:end]
        spectrogram = librosa.feature.melspectrogram(y=chunk,sr=sample_rate)
        spectrogram = resize(np.expand_dims(spectrogram,axis=-1),target_shape)
        data.append(spectrogram)

    return np.array(data)

In [7]:
display(Audio(file_path))

In [6]:
file_path = "./test music/renegade-207649.mp3"
x_test = preprocessdata(file_path)

C:\Users\rizzh\anaconda3\Lib\site-packages\paramiko\pkey.py:82: CryptographyDeprecationWarning: TripleDES has been moved to cryptography.hazmat.decrepit.ciphers.algorithms.TripleDES and will be removed from this module in 48.0.0.
  "cipher": algorithms.TripleDES,
C:\Users\rizzh\anaconda3\Lib\site-packages\paramiko\transport.py:219: CryptographyDeprecationWarning: Blowfish has been moved to cryptography.hazmat.decrepit.ciphers.algorithms.Blowfish and will be removed from this module in 45.0.0.
  "class": algorithms.Blowfish,
C:\Users\rizzh\anaconda3\Lib\site-packages\paramiko\transport.py:243: CryptographyDeprecationWarning: TripleDES has been moved to cryptography.hazmat.decrepit.ciphers.algorithms.TripleDES and will be removed from this module in 48.0.0.
  "class": algorithms.TripleDES,


In [9]:
x_test.shape

(59, 148, 148, 1)

In [10]:
def ModelPrediction(x_test):
    y_predicted = model.predict(x_test)
    predicted_categories = np.argmax(y_predicted,axis=1)
    unique_elements,counts = np.unique(predicted_categories,return_counts=True)
    max_count = np.max(counts)
    max_element = unique_elements[counts == max_count]
    return max_element[0]

In [11]:
class_index = ModelPrediction(x_test)

2/2 ━━━━━━━━━━━━━━━━━━━━ 2s 729ms/step


In [13]:
print("Music Genre :: Model Prediction ----> ", classes[class_index])

Music Genre :: Model Prediction ---->  hiphop
